In [86]:
using LinearAlgebra, Plots, DataFrames, Distributions
import CSV
upscale = 1
default(line = (:steppre, 0.5, 1, 2), size=(800*upscale,600*upscale))
plotly()
include("../KalmanFilter.jl")
import .KalmanFilter


### Messdaten
Im nächsten Schritt generieren wir messdaten.

In [2]:
series = CSV.File("SensorTracker_20181213_154327.csv", delim = ";") |> DataFrame
deletecols!(series, :Proximity)
deletecols!(series, :Light)
deletecols!(series, :Pressure)
first(series, 20)

20×14 DataFrame. Omitted printing of 8 columns
│ Row │ Timestamp       │ Accel_x  │ Accel_y  │ Accel_z  │ Gyro_x   │ Gyro_y   │
│     │ String⍰         │ Float64⍰ │ Float64⍰ │ Float64⍰ │ Float64⍰ │ Float64⍰ │
├─────┼─────────────────┼──────────┼──────────┼──────────┼──────────┼──────────┤
│ 1   │ 20181213_154327 │ 0.227    │ 8.327    │ 4.765    │ 0.118    │ 0.08     │
│ 2   │ 20181213_154327 │ 0.34     │ 9.591    │ 4.7      │ 0.04     │ -0.038   │
│ 3   │ 20181213_154327 │ 1.056    │ 9.235    │ 4.295    │ -0.035   │ 0.076    │
│ 4   │ 20181213_154327 │ -0.347   │ 9.63     │ 4.214    │ 0.112    │ 0.015    │
│ 5   │ 20181213_154327 │ 1.161    │ 8.679    │ 4.264    │ 0.066    │ 0.061    │
│ 6   │ 20181213_154327 │ 0.656    │ 9.757    │ 4.829    │ 0.049    │ 0.062    │
│ 7   │ 20181213_154327 │ 0.67     │ 8.753    │ 4.164    │ 0.041    │ -0.087   │
│ 8   │ 20181213_154327 │ 0.555    │ 8.136    │ 3.565    │ -0.015   │ 0.153    │
│ 9   │ 20181213_154328 │ 0.455    │ 8.761    │ 4.896    │ -0.058   │ 0.057    │
│ 10  │ 20181213_154328 │ 0.177    │ 8.691    │ 3.891    │ -0.049   │ -0.066   │
│ 11  │ 20181213_154328 │ 0.101    │ 8.476    │ 3.563    │ -0.062   │ -0.2     │
│ 12  │ 20181213_154328 │ 0.637    │ 8.354    │ 3.541    │ -0.015   │ 0.059    │
│ 13  │ 20181213_154328 │ 0.115    │ 8.864    │ 3.982    │ 0.03     │ -0.045   │
│ 14  │ 20181213_154328 │ 0.572    │ 7.65     │ 5.284    │ 0.018    │ 0.101    │
│ 15  │ 20181213_154328 │ 0.843    │ 8.655    │ 3.328    │ 0.043    │ 0.026    │
│ 16  │ 20181213_154328 │ 0.113    │ 8.67     │ 4.18     │ -0.023   │ -0.091   │
│ 17  │ 20181213_154329 │ 0.496    │ 8.361    │ 3.412    │ -0.007   │ -0.008   │
│ 18  │ 20181213_154329 │ 0.196    │ 8.689    │ 2.296    │ 0.029    │ -0.042   │
│ 19  │ 20181213_154329 │ 0.747    │ 9.769    │ 4.757    │ 0.088    │ -0.142   │
│ 20  │ 20181213_154329 │ -0.802   │ 8.739    │ 4.247    │ -0.05    │ 0.169    │

In [3]:
describe(series)

14×8 DataFrame. Omitted printing of 3 columns
│ Row │ variable   │ mean        │ min             │ median  │ max             │
│     │ Symbol     │ Union…      │ Any             │ Union…  │ Any             │
├─────┼────────────┼─────────────┼─────────────────┼─────────┼─────────────────┤
│ 1   │ Timestamp  │             │ 20181213_154327 │         │ 20181213_163541 │
│ 2   │ Accel_x    │ 0.276942    │ -5.052          │ 0.225   │ 4.942           │
│ 3   │ Accel_y    │ 8.95713     │ 4.197           │ 8.959   │ 15.125          │
│ 4   │ Accel_z    │ 4.07739     │ -4.319          │ 4.085   │ 14.208          │
│ 5   │ Gyro_x     │ 0.000470847 │ -0.674          │ -0.0    │ 1.019           │
│ 6   │ Gyro_y     │ -0.001933   │ -19.367         │ 0.001   │ 0.456           │
│ 7   │ Gyro_z     │ -0.0067118  │ -11.429         │ -0.005  │ 0.321           │
│ 8   │ Magnetic_x │ 56.8806     │ 3.7             │ 57.2    │ 100.1           │
│ 9   │ Magnetic_y │ -1.02245    │ -104.1          │ 20.1    │ 49.0            │
│ 10  │ Magnetic_z │ -44.5952    │ -133.1          │ -26.5   │ 7.6             │
│ 11  │ Latitude   │ 48.9047     │ 48.817          │ 48.9009 │ 49.0144         │
│ 12  │ Longitude  │ 12.9908     │ 12.6212         │ 13.0167 │ 13.2503         │
│ 13  │ Elevation  │ 535.134     │ 373.8           │ 534.2   │ 890.7           │
│ 14  │ Speed      │ 78.5058     │ 0.0             │ 76.1    │ 138.3           │

Wir kalibrieren die Beschleunigungssensoren:

In [4]:
plot(series[:Accel_x], label = "Accel_x")
plot!(series[:Accel_y], label = "Accel_y")
plot!(series[:Accel_z], label = "Accel_z")

### Glättung der X-Achse

In [5]:
# Populationsmittelwert wird abgelesen
median_x = 0.276942
# Damit berechnen wir die empirische Varianz
var_accel_x = 1/length(series[:Accel_x]) * reduce(+, map(x -> (x - median_x)^2, series[:Accel_x]))

0.8023490574157556

In [87]:
y_x = series[8200:8500, :Accel_x]
y_y = series[8200:8500, :Accel_y]
y_z = series[8200:8500, :Accel_z]

y = [y_x y_y y_z]
x = collect(1:size(y)[1])

A = [.7 0 0; 0 .7 0; 0 0 .7] # Zustandsübergangsmatrix
Q = [.4 0 0; 0 .5 0; 0 0 .5]

G = [.8 0 0; 0 .8 0; 0 0 .8] # Messabbildung Matrix
R = [.4 0 0; 0 .4 0; 0 0 .4]

x̂_0 = [0; 0; 0]
# x̂_0 = f(1)
Σ_0 = [.1 0 0; 0 .1 0; 0 0 .1]

model = KalmanFilter.Kalman(A, Q, G, R, x̂_0, Σ_0)

y_filtered = zeros(3, length(x))
y_predicted = zeros(3, length(x))
y_k = zeros(3, length(x))
for (index, value) in enumerate(x)
    y_cur = y[index, :]
    
    fusioned = KalmanFilter.fusion(model, y_cur)
    y_filtered[:, index] = fusioned[1]
    
    predicted = KalmanFilter.predict(model)
    y_predicted[:, index] = predicted[1]
end
error = y_filtered' - y
@show sum(error, dims = 1)
@show sum(error) / size(y)[1]

sum(error, dims=1) = [-43.6178 -85.9557 -36.4418]
sum(error) / (size(y))[1] = -0.5515457757709569


-0.5515457757709569

In [88]:
plot(x, y_predicted', label = "Predicted", linestyle=:dash)
plot!(x, y_filtered', label = "Filtered")
plot!(x, y, label = "Ground Thruth", linestyle = :dot)

In [112]:
y_x_gyro = series[8200:9000, :Gyro_x]
y_y_gyro = series[8200:9000, :Gyro_y]
y_z_gyro = series[8200:9000, :Gyro_z]

y_gyro = [y_x_gyro y_y_gyro y_z_gyro]
x = collect(1:size(y_gyro)[1])

A = [1 0 0; 0 1 0; 0 0 1] # Zustandsübergangsmatrix
Q = [.3 0 0; 0 .3 0; 0 0 .3]

G = [1 0 0; 0 1 0; 0 0 1] # Messabbildung Matrix
R = [1.8 0 0; 0 1.8 0; 0 0 1.8]

x̂_0 = [1; 1; 1]
Σ_0 = [.1 0 0; 0 .1 0; 0 0 .1]

model = KalmanFilter.Kalman(A, Q, G, R, x̂_0, Σ_0)

y_filtered_gyro = zeros(3, length(x))
y_predicted_gyro = zeros(3, length(x))
for (index, value) in enumerate(x)
    y_cur = y_gyro[index, :]

    fusioned = KalmanFilter.fusion(model, y_cur)
    y_filtered_gyro[:, index] = fusioned[1]
    
    predicted = KalmanFilter.predict(model)
    y_predicted_gyro[:, index] = predicted[1]
end
error = y_filtered' - y
@show sum(error, dims = 1)
@show sum(error) / size(y)[1]

BoundsError: BoundsError: attempt to access 3×801 Array{Float64,2} at index [Base.Slice(Base.OneTo(3)), 802]

In [111]:
plot(x, y_predicted_gyro', label = "Predicted", linestyle=:dash)
plot!(x, y_filtered_gyro', label = "Filtered")
plot!(x, y_gyro, label = "Ground Thruth", linestyle = :dot)